In [ ]:
!cd .. && make clean

rm -rf build


In [1]:
!cd .. && make cia-unpack

Running unpacking tool.
bin/unpack.sh cias/bd.cia build/dev
~/projects/bravely-default-mod/build/dev ~/projects/bravely-default-mod
[1] Extracting CIA with ctrtool to build/dev
CiaHeader:
|- HeaderSize:      0x2020
|- Type:            Normal (0x0000)
|- FormatVersion:   Cia (0x0000)
|- CertificateSize: 0xa00
|- TicketSize:      0x350
|- TitleMetaSize:   0xb64
|- FooterSize:      0x3ac0
|- ContentSize:     0xcef27000
\- EnabledContent:
   |- 0x0000
   \- 0x0001
Certificate Chain:
|- Certificate 0:
|  |- DigitalSignature: 
|  |  |- SigType:    RSA-4096-SHA256 (0x10003)
|  |  |- Issuer:     Root
|  |  \- Signature:  704138EF...61CB4C2E
|  |- Subject:       CA00000003
|  \- PublicKey:     RSA-2048 (0x1)
|     |- m:          B279C9E2...EBEED379
|     \- e:          00010001
|- Certificate 1:
|  |- DigitalSignature: 
|  |  |- SigType:    RSA-2048-SHA256 (0x10004)
|  |  |- Issuer:     Root-CA00000003
|  |  \- Signature:  919EBE46...08847982
|  |- Subject:       XS0000000c
|  \- PublicKey:    

In [2]:
!cd .. && MAMBA_ROOT_PREFIX=/home/struktured/micromamba make crowd-unpack

micromamba run -n "bd-dev" bin/crowd.sh -r build/dev -o build/crowd-dev-unpacked -g BD unpack
Output directory: build/crowd-dev-unpacked
Output directory: /home/struktured/projects/bravely-default-mod/build/crowd-dev-unpacked
INFO:arcanist.crowd.core.rom:Loading table from content.0000.cxi.0000.00000000 with fmt xls
INFO:arcanist.crowd.core.rom:Loaded content.0000.cxi.0000.00000000
INFO:arcanist.crowd.core.rom:Loading table from content.0000.cxi.0001.00000001 with fmt xls
INFO:arcanist.crowd.core.rom:Loaded content.0000.cxi.0001.00000001
INFO:arcanist.crowd.core.rom:Loading table from cxi/exefs.bin with fmt xls
INFO:arcanist.crowd.core.rom:Loaded cxi/exefs.bin
INFO:arcanist.crowd.core.rom:Loading table from cxi/header.bin with fmt xls
INFO:arcanist.crowd.core.rom:Loaded cxi/header.bin
INFO:arcanist.crowd.core.rom:Loading table from cxi/plain.bin with fmt xls
INFO:arcanist.crowd.core.rom:Loaded cxi/plain.bin
INFO:arcanist.crowd.core.rom:Loading table from cxi/romfs.bin with fmt xls
INFO

In [3]:
import sys
sys.path.insert(0, "../")

import arcanist
from arcanist.crowd import loader
import importlib
importlib.reload(arcanist)
importlib.reload(loader)

CROWD_DATA="../build/crowd-dev-unpacked"
PAT = "BuffLimit"

data = loader.annotate(crowd_data=CROWD_DATA, pat=PAT)


In [4]:
import pandas as pd
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

files : list[str] = []
schemas :list[str]= []
for k,v in data.items():    
    for schema in v.keys():
        files.append(k)
        schemas.append(schema)

files_schemas = pd.DataFrame({'files':  files, 'schemas': schemas})

pd.DataFrame({'unique': files_schemas[files_schemas['files'].str.contains('Common_en')].files.unique()}) # type: ignore

unique
0  Common_en/Battle

In [5]:
battle_data = data['Common_en/Battle']
battle_data['BuffLimit.btb']

Unnamed: 0  Unnamed: 1  Unnamed: 2  Unnamed: 3  Unnamed: 4  Unnamed: 5  \
0         150         150         150         150         150         150   
1          75          75          75          75          75          75   

   Unnamed: 6  Unnamed: 7  Unnamed: 8  Unnamed: 9  Unnamed: 10  Unnamed: 11  \
0        1000         150         700         700          150          200   
1          75          75          10          10           75           75   

   Unnamed: 12  
0          200  
1           75

In [6]:

from arcanist.crowd.loader import CrowdSchemaOverrides


battle_data = ["Common_en/Battle"]

overrides : list[CrowdSchemaOverrides] = []
for path in battle_data:
    overrides.append(CrowdSchemaOverrides.builder(path).add(\
              sheet="BuffLimit.btb", 
              index={0: 'MaxPercent', 1:'MinPercent'}, 
              columns={0:'PhysicalAttack', 1: 'MagicAttack', 2: 'PhysicalDefense', 3: 'MagicDefense', 4: 'CriticalHit', 5: 'Speed', 6: 'HitCount'}
    ).build())

print(overrides)
annot=loader.annotate(crowd_data=data, overrides=overrides)


[CrowdSchemaOverrides(path='Common_en/Battle', schemas=[CrowdSchema(sheet='BuffLimit.btb', index={0: 'MaxPercent', 1: 'MinPercent'}, columns={0: 'PhysicalAttack', 1: 'MagicAttack', 2: 'PhysicalDefense', 3: 'MagicDefense', 4: 'CriticalHit', 5: 'Speed', 6: 'HitCount'})])]
Renamed column Unnamed: 0 to PhysicalAttack in sheet BuffLimit.btb.
Renamed column Unnamed: 1 to MagicAttack in sheet BuffLimit.btb.
Renamed column Unnamed: 2 to PhysicalDefense in sheet BuffLimit.btb.
Renamed column Unnamed: 3 to MagicDefense in sheet BuffLimit.btb.
Renamed column Unnamed: 4 to CriticalHit in sheet BuffLimit.btb.
Renamed column Unnamed: 5 to Speed in sheet BuffLimit.btb.
Renamed column Unnamed: 6 to HitCount in sheet BuffLimit.btb.
Renamed index 0 to MaxPercent in dataset BuffLimit.btb.
Renamed index 1 to MinPercent in dataset BuffLimit.btb.


In [7]:

for path in battle_data:
    buff_limits = annot[path]['BuffLimit.btb']
    buff_limits.loc['MaxPercent', 'PhysicalAttack'] = buff_limits['PhysicalAttack']['MaxPercent']*2 + 1
    buff_limits.loc['MaxPercent', 'MagicAttack'] = buff_limits['MagicAttack']['MaxPercent']*2 + 2
    buff_limits.loc['MaxPercent', 'PhysicalDefense'] = buff_limits['PhysicalDefense']['MaxPercent']*2 + 3
    buff_limits.loc['MaxPercent', 'MagicDefense'] = buff_limits['MagicDefense']['MaxPercent']*2 + 4
    buff_limits.loc['MaxPercent', 'CriticalHit'] = buff_limits['CriticalHit']['MaxPercent']*2 + 5
    buff_limits.loc['MaxPercent', 'Speed'] = buff_limits['Speed']['MaxPercent']*2 + 6
    buff_limits.loc['MaxPercent', 'HitCount'] = buff_limits['HitCount']['MaxPercent']*2 + 7




In [8]:
buff_limits

PhysicalAttack  MagicAttack  PhysicalDefense  MagicDefense  \
MaxPercent             301          302              303           304   
MinPercent              75           75               75            75   

            CriticalHit  Speed  HitCount  Unnamed: 7  Unnamed: 8  Unnamed: 9  \
MaxPercent          305    306      2007         150         700         700   
MinPercent           75     75        75          75          10          10   

            Unnamed: 10  Unnamed: 11  Unnamed: 12  
MaxPercent          150          200          200  
MinPercent           75           75           75

In [9]:
import importlib
importlib.reload(loader)
for key in set(annot.keys()):
    if key != 'Common_en/Battle':
        del annot[key]

loader.save(annot, root_dir=CROWD_DATA, fmt="xls")

Saved crowd data to ../build/crowd-dev-unpacked/cxi/romfs_dir/Common_en/Battle/crowd.xls


In [ ]:
!cd .. && MAMBA_ROOT_PREFIX=/home/struktured/micromamba make crowd-pack

micromamba run -n "bd-dev" bin/crowd.sh -r build/crowd-dev-unpacked -o build/crowd-dev-packed -g BD pack
Output directory: build/crowd-dev-packed
Output directory: /home/struktured/projects/bravely-default-mod/build/crowd-dev-packed
Packing....
CHDIR: /home/struktured/projects/bravely-default-mod/build/crowd-dev-unpacked
INFO:root:No  in {'cxi/romfs_dir/Common_fr/DReportTable': ['DarkKnightNoteData.btb', 'DarkKnightNoteIndex.btb', 'DTableBonusData.btb', 'DTableItemData.btb', 'DTableMonsterData.btb', 'GenomData.btb', 'GenomFlag.btb', 'GeographyData.btb', 'GeographyFlag.btb', 'GeographyIndex.btb', 'KeywordData.btb', 'KeywordFlag.btb', 'KeywordIndex.btb', 'MemoirData.btb', 'MemoirIndex.btb', 'MixData.btb', 'MixFlag.btb', 'NoteData.btb', 'NoteFlag.btb', 'NoteIndex.btb', 'PersonData.btb', 'PersonFlag.btb', 'PersonIndex.btb'], 'cxi/romfs_dir/Common_fr/PartyChat': ['MP_LoopTable.btb', 'MP_UcaTable.btb', 'PartyChatScript0.btb', 'PartyChatScript1.btb', 'PartyChatScript2.btb', 'PartyChatScript3.

In [ ]:
!cd .. && make deploy-romfs

QUALIFIER=dev USER=carm BUILD_DIR=build CITRA_DIR=/data/citra/citra-emu bin/deploy_romfs.sh
+ VERSION=00040000000FC500
+ QUALIFIER=dev
+ ROMFS_DIR=build/crowd-dev-packed/00040000000FC500/romfs
+ CITRA_DIR=/data/citra/citra-emu
++ date +%Y%m%d_%H%M%S
+ BACKUP=20250809_172437
+ BACKUP_DIR=build/dev/backup
+ FROM=
+ TO=/data/citra/citra-emu/load/mods/00040000000FC500/romfs
+ mkdir -p build/dev/backup
+ [[ -z '' ]]
+ FROM=build/crowd-dev-packed/00040000000FC500/romfs
+ echo Using default from build/crowd-dev-packed/00040000000FC500/romfs
Using default from build/crowd-dev-packed/00040000000FC500/romfs
+ set +e
+ mkdir -p /data/citra/citra-emu/load/mods/00040000000FC500/romfs
+ set -e
+ echo 'Backing up original romfs'
Backing up original romfs
+ cp -r -v /data/citra/citra-emu/load/mods/00040000000FC500/romfs build/dev/backup/romfs_dir.20250809_172437.bak
'/data/citra/citra-emu/load/mods/00040000000FC500/romfs' -> 'build/dev/backup/romfs_dir.20250809_172437.bak'
'/data/citra/citra-emu/load/

In [ ]:

!cd .. && make deploy-code

QUALIFIER=dev USER=carm BUILD_DIR=build CITRA_DIR=/data/citra/citra-emu bin/deploy_code.sh 
+ QUALIFIER=dev
+ EXEFS_DIR=build/crowd-dev-unpacked/cxi/exefs_dir
+ CITRA_DIR=/data/citra/citra-emu
++ date +%Y%m%d_%H%M%S
+ BACKUP=20250809_172437
+ VERSION=00040000000FC500
+ BACKUP_DIR=build/dev/backup
+ FROM=
+ TO=/data/citra/citra-emu/load/mods/00040000000FC500/exefs/code.bin
+ mkdir -p build/dev/backup
+ [[ -z '' ]]
+ FROM=build/crowd-dev-unpacked/cxi/exefs_dir/code.bin
+ echo Using default from build/crowd-dev-unpacked/cxi/exefs_dir/code.bin
Using default from build/crowd-dev-unpacked/cxi/exefs_dir/code.bin
+ echo 'Backing up original code.bin'
Backing up original code.bin
+ cp -v /data/citra/citra-emu/load/mods/00040000000FC500/exefs/code.bin build/dev/backup/code.bin.20250809_172437.bak
'/data/citra/citra-emu/load/mods/00040000000FC500/exefs/code.bin' -> 'build/dev/backup/code.bin.20250809_172437.bak'
+ echo 'Deploying new code.bin'
Deploying new code.bin
+ cp -v build/crowd-dev-unpack